In [2]:
import random
from graph_data_loader import GraphDataLoader
from query_generator import QueryGenerator
import graph_pricing_transaciton
from graph_pricing_transaciton import TransactionManager
from graph_pricing_transaciton import FullTransactionLogger
from  graph_pricing_transaciton import TransactionEvaluator
import networkx as nx
import time
import pickle

In [2]:
import rdflib
import pickle
import networkx as nx
import igraph as ig

class GraphDataLoader:
    """
    A class for loading RDF graph data into a NetworkX undirected graph,
    and loading pre-split subgraphs (also as NetworkX undirected graphs).
    """

    def __init__(self, rdf_file, subgraph_file):
        """
        :param rdf_file: Path to RDF TTL file
        :param subgraph_file: Path to the pickled subgraph dataset
        """
        self.rdf_file = rdf_file
        self.subgraph_file = subgraph_file
        self.graph = nx.Graph()  # NetworkX undirected graph
        self.subgraphs = []

    def load_graph(self):
        """
        Load RDF data and construct a NetworkX undirected graph.

        加载 RDF 数据并构建 NetworkX 无向图。
        """
        rdf_graph = rdflib.Graph()
        rdf_graph.parse(self.rdf_file, format="ttl")

        for subj, pred, obj in rdf_graph:
            s = subj.split('/')[-1]
            p = pred.split('/')[-1]
            o = obj.split('/')[-1]

            # Skip self-loops
            if s == o:
                continue

            # Add nodes with 'name' attribute if not already present
            if s not in self.graph:
                self.graph.add_node(s, name=s)
            if o not in self.graph:
                self.graph.add_node(o, name=o)

            # Add edge with 'label' attribute
            if not self.graph.has_edge(s, o):
                self.graph.add_edge(s, o, label=p)
            else:
                # Support multiple labels between same nodes
                existing_label = self.graph[s][o]['label']
                if isinstance(existing_label, list):
                    if p not in existing_label:
                        existing_label.append(p)
                else:
                    if p != existing_label:
                        self.graph[s][o]['label'] = [existing_label, p]

    def load_subgraphs(self):
        """
        Load precomputed subgraphs and convert to NetworkX undirected graphs.

        加载已预处理的子图（统一转换为 NetworkX 无向图，并确保属性）。
        """
        with open(self.subgraph_file, 'rb') as f:
            raw_subgraphs = pickle.load(f)

        self.subgraphs = []
        for subG in raw_subgraphs:
            # Convert to networkx.Graph
            if isinstance(subG, ig.Graph):
                subG = subG.to_networkx()
            elif isinstance(subG, (nx.DiGraph, nx.MultiDiGraph)):
                subG = nx.Graph(subG)
            elif not isinstance(subG, nx.Graph):
                raise TypeError(f"Invalid subgraph type: {type(subG)}")

            # Add missing node 'name' attributes
            for node in subG.nodes:
                if 'name' not in subG.nodes[node]:
                    subG.nodes[node]['name'] = str(node)

            # Add missing edge 'label' attributes
            for i, (u, v) in enumerate(subG.edges):
                if 'label' not in subG.edges[u, v]:
                    subG.edges[u, v]['label'] = f"edge_{i}"

            self.subgraphs.append(subG)

    def get_graph(self):
        """
        Return the main RDF-based graph (NetworkX undirected graph).
        """
        return self.graph

    def get_subgraphs(self):
        """
        Return the list of subgraphs (each as NetworkX undirected graph).
        """
        return self.subgraphs


In [ ]:
def convert_igraph_to_networkx(ig_graph):
    """
    将 igraph.Graph 转换为 networkx.DiGraph（有向图）

    :param ig_graph: igraph.Graph（可能是有向或无向）
    :return: networkx.DiGraph
    """
    nx_graph = nx.DiGraph()  # 确保是有向图

    # 添加节点及其属性
    for v in ig_graph.vs:
        nx_graph.add_node(v.index, **v.attributes())

    # 添加边及其属性
    for e in ig_graph.es:
        nx_graph.add_edge(e.source, e.target, **e.attributes())

    return nx_graph

In [3]:
#dbpedia数据集
loader = GraphDataLoader("dbpedia.ttl", "subgraphs.pkl")
loader.load_graph()
loader.load_subgraphs()
G = loader.get_graph()
print("Graph loaded with", len(G.nodes), "nodes and", len(G.edges), "edges.")
subgraphs = loader.get_subgraphs()
# subgraphs = []
# for subG in subgraphs_ig:
#     subg = convert_igraph_to_networkx(subG)
#     subgraphs.append(subg)
print(len(subgraphs))

Graph loaded with 78273 nodes and 68756 edges.
73890


In [ ]:
#---------------------------------------中心性------------------------------------------

In [4]:
# version2.1 时间优化名字版
def compute_named_vertex_and_edge_centrality(G):
    """
    计算图 G 中以顶点 'name' 属性为键的 Degree Centrality 和边的 Edge Betweenness Centrality。

    :param G: NetworkX 图（节点需包含 'name' 属性）
    :return: (vertex_centrality_dict, edge_centrality_dict)
    """
    # 提前构建 ID -> name 映射，避免多次查找
    id_to_name = {node_id: G.nodes[node_id].get('name', node_id) for node_id in G.nodes}

    # 顶点中心性
    raw_vertex_centrality = nx.degree_centrality(G)
    vertex_centrality_named = {
        id_to_name[node_id]: centrality
        for node_id, centrality in raw_vertex_centrality.items()
    }

    # 边介数中心性
    raw_edge_centrality = nx.edge_betweenness_centrality(G, normalized=True)
    edge_centrality_named = {
        tuple(sorted((id_to_name[u], id_to_name[v]))): centrality
        for (u, v), centrality in raw_edge_centrality.items()
    }

    return vertex_centrality_named, edge_centrality_named

In [5]:
v_centrality, e_centrality = compute_named_vertex_and_edge_centrality(G)

print("顶点中心性（按 name）:")
print(v_centrality)

print("\n边中心性（按 name 对）:")
print(e_centrality)

顶点中心性（按 name）:
{'Down_with_the_Clique': 1.277596075224857e-05, 'Chicago_Recording_Company': 0.0001660874897792314, 'Penn_State_College_of_Arts_and_Architecture': 1.277596075224857e-05, 'University_Park,_Pennsylvania': 0.00048548650858544566, 'Eddie_Drummond': 1.277596075224857e-05, 'Wheeling,_West_Virginia': 8.943172526574e-05, 'Jakapur_Dam': 1.277596075224857e-05, 'India': 0.004561017988552739, 'James_Lowe_(footballer)': 1.277596075224857e-05, 'Scotland_national_football_team': 0.017630825838103027, 'Louis_Néel': 1.277596075224857e-05, 'Grenoble': 7.665576451349142e-05, 'Edmonton_Radial_Railway__Edmonton_Radial_Railway__1': 1.277596075224857e-05, 'Edmonton': 0.00062602207686018, 'Smyk_Department_Store': 1.277596075224857e-05, 'Poland': 0.00039605478331970566, 'Postcrypt_Coffeehouse': 1.277596075224857e-05, 'Columbia_University': 0.00015331152902698283, 'Qi_Wusheng': 1.277596075224857e-05, 'China_national_football_team': 0.0022868969746524938, 'Rony_Azar': 1.277596075224857e-05, 'Leban

In [ ]:
import pickle
import os

def save_centrality_to_file(vertex_centrality, edge_centrality, filename):
    """
    将中心性结果保存到文件
    """
    with open(filename, 'wb') as f:
        pickle.dump((vertex_centrality, edge_centrality), f)

def load_centrality_from_file(filename):
    """
    从文件中加载中心性结果
    """
    with open(filename, 'rb') as f:
        vertex_centrality, edge_centrality = pickle.load(f)
    return vertex_centrality, edge_centrality

In [ ]:
#中心性计算并存储
def compute_or_load_centrality(G, cache_file='my_graph_centrality.pkl'):
    """
    如果缓存文件存在，则加载中心性；否则计算并保存。
    """
    if os.path.exists(cache_file):
        print(f"加载缓存中心性数据: {cache_file}")
        return load_centrality_from_file(cache_file)
    else:
        print("计算中心性...")
        vertex_centrality, edge_centrality = compute_named_vertex_and_edge_centrality(G)
        save_centrality_to_file(vertex_centrality, edge_centrality, cache_file)
        print(f"中心性已保存到缓存文件: {cache_file}")
        return vertex_centrality, edge_centrality

In [3]:

#中心性文件读取
def load_centrality_from_file(filename):
    """
    从缓存文件中加载 vertex 和 edge 中心性字典
    """
    with open(filename, 'rb') as f:
        vertex_centrality, edge_centrality = pickle.load(f)
    return vertex_centrality, edge_centrality

# 实际调用
vertex_centrality, edge_centrality = load_centrality_from_file('my_graph_centrality.pkl')

In [ ]:
#交易频率计算
from collections import defaultdict

def compute_transaction_frequency_from_all_subgraphs(G, all_subgraphs):
    """
    从所有交易子图（成功 + 失败）中计算节点和边的交易频率。

    :param G: 主图（NetworkX 图）
    :param all_subgraphs: List of NetworkX 子图，表示历史交易（成功+失败）
    :return: (vertex_freq, edge_freq)
    """
    T = len(all_subgraphs)  # 总交易尝试数

    vertex_freq = defaultdict(int)
    edge_freq = defaultdict(int)

    for sg in all_subgraphs:
        for node in sg.nodes:
            name = sg.nodes[node].get('name', node)
            vertex_freq[name] += 1

        for u, v in sg.edges:
            name_u = sg.nodes[u].get('name', u)
            name_v = sg.nodes[v].get('name', v)
            edge_key = tuple(sorted((name_u, name_v)))  # 无向边按排序后的名字
            edge_freq[edge_key] += 1

    # 归一化：转为频率
    for name in vertex_freq:
        vertex_freq[name] /= T
    for edge in edge_freq:
        edge_freq[edge] /= T
    return vertex_freq, edge_freq

In [ ]:
#根据交易历史得到全部交易的子图列表

# all_subgraphs = 成交 + 失败的交易子图列表（每个为 networkx 图）
#计算交易频率
vertex_tf, edge_tf = compute_transaction_frequency_from_all_subgraphs(G, all_subgraphs)

print("节点 A 的交易频率：", vertex_tf.get('A', 0.0))
print("边 (A, B) 的交易频率：", edge_tf.get(('A', 'B'), 0.0))
#综合成本、交易频率和中心性更新价格

In [ ]:
#————————————————————————————————————————————————————————————————————————废代码-----------------------------------------------------------

In [ ]:
#version2.0 名字版
def compute_named_vertex_and_edge_centrality(G):
    """
    计算图 G 中以顶点 'name' 属性为键的 Degree Centrality 和边的 Edge Betweenness Centrality。

    :param G: NetworkX 图（节点需包含 'name' 属性）
    :return: (vertex_centrality_dict, edge_centrality_dict)
    """
    # 原始中心性计算
    raw_vertex_centrality = nx.degree_centrality(G)
    raw_edge_centrality = nx.edge_betweenness_centrality(G, normalized=True)

    # 顶点使用 name 属性作为键
    vertex_centrality_named = {}
    for node_id, centrality in raw_vertex_centrality.items():
        node_name = G.nodes[node_id].get('name', node_id)
        vertex_centrality_named[node_name] = centrality

    # 边使用 (name1, name2) 作为键（无向图可用 tuple 排序处理对称性）
    edge_centrality_named = {}
    for (u, v), centrality in raw_edge_centrality.items():
        name_u = G.nodes[u].get('name', u)
        name_v = G.nodes[v].get('name', v)
        edge_key = tuple(sorted((name_u, name_v)))  # 确保无向边的顺序一致
        edge_centrality_named[edge_key] = centrality

    return vertex_centrality_named, edge_centrality_named

In [ ]:
#version1.0 序号版
def compute_vertex_and_edge_centrality(G):
    """
    计算图 G 中的顶点 Degree Centrality 和边的 Edge Betweenness Centrality。

    :param G: NetworkX 图
    :return: (vertex_centrality_dict, edge_centrality_dict)
    """
    # 顶点 Degree Centrality（默认归一化）
    vertex_centrality = nx.degree_centrality(G)

    # 边 Edge Betweenness Centrality（默认归一化）
    edge_centrality = nx.edge_betweenness_centrality(G, normalized=True)

    return vertex_centrality, edge_centrality

In [ ]:
G = nx.karate_club_graph()  # 示例图
v_centrality, e_centrality = compute_vertex_and_edge_centrality(G)

In [ ]:

print("顶点中心性示例:")
for node, centrality in list(v_centrality.items())[:5]:
    print(f"节点 {node}: 中心性 = {centrality:.4f}")